In [13]:
## Basic stuff
%load_ext autoreload
%autoreload
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))
display(HTML("""<style>div.output_area{max-height:10000px;overflow:scroll;}</style>"""))

## Python Version
import sys
print("Python: {0}".format(sys.version))

################################################################################
## General Stuff
################################################################################
from ioUtils import saveJoblib, loadJoblib, saveFile, getFile
import urllib
from urllib.parse import quote
from collection import collections
from timeUtils import clock, elapsed
from fsUtils import moveFile, setFile, setDir, setSubDir, isFile, isDir, mkDir
from pandasUtils import getRowDataByColValue, getRowData
from fileUtils import getFileBasics, getBasename
from time import sleep
import time
from multiprocessing import Pool


################################################################################
## Music Stuff
################################################################################

## General
from discogsBase import discogs
from masterdb import getArtistAlbumsDB, discConv

## Discogs
from artist import artist
from artists import artists
from discogsUtils import discogsUtils
from albums import albums

## AllMusic
from artistAM import artistAM
from artistsAM import artistsAM
from discogsUtils import allmusicUtils
from artistsAM import artistsAM

## MusicBrainz
from artistMB import artistMB
from artistsMB import artistsMB
from discogsUtils import musicbrainzUtils



import datetime as dt
start = dt.datetime.now()
print("Notebook Last Run Initiated: "+str(start))

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


Python: 3.7.3 (default, Mar 27 2019, 16:54:48) 
[Clang 4.0.1 (tags/RELEASE_401/final)]
Notebook Last Run Initiated: 2020-03-06 18:05:20.420613


# Global Variables

In [2]:
dbFull  = ["Discogs", "AllMusic", "MusicBrainz"]
dbNames = [x.lower() for x in dbFull]
dbKeys  = []
for item in list(zip(dbFull, dbNames)):
    dbKeys.append({"Key": item[0], "Name": item[1]})

[{'Key': 'Discogs', 'Name': 'discogs'}, {'Key': 'AllMusic', 'Name': 'allmusic'}, {'Key': 'MusicBrainz', 'Name': 'musicbrainz'}]


# Set All Databases

In [6]:
disc = {}
discdf  = {}
artists = {}
artistIDToName = {}
artistNameToID = {}
artistAlbumsDB = {}
for dbKey in dbKeys:
    key  = dbKey["Key"]
    name = dbKey["Name"]
    disc[key] = discogs(name)
    
    print("Getting Master Artist DB File ({0})".format(key))
    
    discdf[key]  = disc[key].getMasterSlimArtistDiscogsDB()
    artists[key] = [x for x in list(discdf[key]["DiscArtist"]) if x is not None]
    print("  Found {0} Artists in DB".format(len(artists[key])))

    artistIDToName[key] = discdf[key]["DiscArtist"].to_dict()
    artistNameToID[key] = {}
    print("  Found {0} ID -> Name entries".format(len(artistIDToName[key])))
                        
    for artistID,artistName in artistIDToName[key].items():
        if artistName is None:
            continue
        if artistNameToID[key].get(artistName) is None:
            artistNameToID[key][artistName] = []
        artistNameToID[key][artistName].append(artistID)
    print("  Found {0} Name -> ID entries".format(len(artistNameToID[key])))

    artistAlbumsDB[key] = getArtistAlbumsDB(disc[key], force=False)
    print("  Found {0} Artist Albums".format(artistAlbumsDB[key].shape[0]))
    print("")
    
_, _ = clock("Last Run")

Getting Master Artist DB File (Discogs)
  Found 717391 Artists in DB
  Found 717391 ID -> Name entries
  Found 659367 Name -> ID entries
Current Time is Fri Mar 06, 2020 17:50:23 for 
=================================== Creating Artist Albums DB ===================================
Using previously created Artist Albums DB
Current Time is Fri Mar 06, 2020 17:51:00 for Done with 
=================================== Creating Artist Albums DB ===================================
Process [Done with 
=================================== Creating Artist Albums DB ===================================] took 37 seconds.
  Found 717391 Artist Albums

Getting Master Artist DB File (AllMusic)
  Found 38575 Artists in DB
  Found 38575 ID -> Name entries
  Found 36297 Name -> ID entries
Current Time is Fri Mar 06, 2020 17:51:01 for 
=================================== Creating Artist Albums DB ===================================
Using previously created Artist Albums DB
Current Time is Fri Mar 06, 2020 

# Get Music DB Map

In [9]:
def getMyMusicDBMap():
    myMusicMap = getFile(ifile="/Users/tgadfort/Documents/code/music/myMusicMap.p")
    print("Found {0} entries".format(len(myMusicMap)))
    return myMusicMap


def showMyMusicMap(myMusicMap):
    cntrs = {"Discogs": 0, "AllMusic": 0, "MusicBrainz": 0}
    for myArtistName, myArtistData in myMusicMap.items():
        if myArtistData["Discogs"] is not None:
            cntrs["Discogs"] += 1
        if myArtistData["AllMusic"] is not None:
            cntrs["AllMusic"] += 1
        if myArtistData["MusicBrainz"] is not None:
            cntrs["MusicBrainz"] += 1
    print(cntrs)

In [10]:
myMusicMap = getMyMusicDBMap()
showMyMusicMap(myMusicMap)

Found 4756 entries
{'Discogs': 4733, 'AllMusic': 4473, 'MusicBrainz': 3372}


In [21]:
## Basic stuff
%load_ext autoreload
%autoreload
from mainDB import getOrganizedDBArtistAlbums, getAlbumTypes

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [155]:
from searchUtils import findNearest
num    = 1
cutoff = 0.9
musicArtists  = list(myMusicMap.keys())

albumTypeKeys = getAlbumTypes(None, keys=True)

try:
    albumDBMap    = getFile("masterDBMap.p")
except:
    albumDBMap    = {}

print("{0: <40}{1: <10}{2: <10}{3}".format("Artist Name", "# Albums", "# Missing", "# Possible IDs"))
for artistName in musicArtists:
    if albumDBMap.get(artistName) is None:
        print("==> Artist {0}".format(artistName))
        albumDBMap[artistName] = {}
        
    matchValues = myMusicMap[artistName]
    #dbAlbums    = {k: {} for k in albumTypeKeys}
    dbAlbums = {}

    myDBAlbums = dict(zip(albumTypeKeys, {}))
    for dbKey in dbKeys:
        key        = dbKey['Key']
        matchValue = matchValues[key]
        if matchValue is not None:
            possibleID   = matchValue["ID"]
            artistAlbums = getRowData(artistAlbumsDB[key], rownames=possibleID)['Albums']
            albums       = getOrganizedDBArtistAlbums(artistAlbums, key)
            dbAlbums[key] = albums
           
    if len(dbAlbums) >= 2:
        dbRanking = ["MusicBrainz", "AllMusic", "Discogs"]
        primary   = {}
        seconary  = None        
        for ir, dbRank in enumerate(dbRanking):
            if dbAlbums.get(dbRank) is not None:
                primaryDB     = dbRank
                primaryAlbums = dbAlbums[dbRank]
                secondary     = [dbRanking[i] for i in range(ir+1, len(dbRanking)) if dbAlbums.get(dbRanking[i]) is not None]
                break

        for albumType in albumTypeKeys:
            try:
                int(albumType)
            except:
                continue
            if albumDBMap[artistName].get(albumType) is None:
                print("   ==> Album Type {0}".format(albumType))
                albumDBMap[artistName][albumType] = {}

            for albumName in primaryAlbums[albumType]:
                primaryValue  = {"DB": primaryDB, "Name": albumName}
                if albumDBMap[artistName][albumType].get(albumName) is None:
                    print("\t==> Album Name {0}".format(albumName))
                    albumDBMap[artistName][albumType][albumName] = {"DB": primaryDB, "Match": {}}
                    secondaryMatches = []
                else:
                    secondaryMatches = []
                    for k,v in albumDBMap[artistName][albumType].items():
                        secondaryMatches += [v2 for k2,v2 in v["Match"].items() if v2 is not None]
                        
                for key in secondary:
                    if albumDBMap[artistName][albumType][albumName]["Match"].get(key) is not None:
                        continue
                    secondaryAlbums = dbAlbums[key][albumType]
                    secondaryAlbums = list(set(secondaryAlbums).difference(set(secondaryMatches)))
                    albumMatches    = findNearest(albumName, secondaryAlbums, num, cutoff)
                    if len(albumMatches) > 0:
                        dstAlbum   = albumMatches[0]
                        secondaryMatches.append(dstAlbum)
                        albumDBMap[artistName][albumType][albumName]["Match"][key] = dstAlbum
                        print("\t   ==> Album Match {0}".format(albumDBMap[artistName][albumType][albumName]["Match"]))

saveFile(idata=albumDBMap, ifile="masterDBMap.p", debug=True)

Artist Name                             # Albums  # Missing # Possible IDs
==> Artist A Flock Of Seagulls
   ==> Album Type 1
	==> Album Name A Flock of Seagulls
	   ==> Album Match {'Discogs': 'A Flock Of Seagulls'}
	==> Album Name Listen
	   ==> Album Match {'Discogs': 'Listen'}
	==> Album Name The Story of a Young Heart
	   ==> Album Match {'Discogs': 'The Story Of A Young Heart'}
	==> Album Name Dream Come True
	   ==> Album Match {'Discogs': 'Dream Come True'}
	==> Album Name Light at the End of the World
	==> Album Name Ascension
	   ==> Album Match {'Discogs': 'Ascension'}
   ==> Album Type 2
	==> Album Name The Best of A Flock of Seagulls [Jive]
	==> Album Name Greatest Hits [Jive]
	==> Album Name Collection
	==> Album Name 20 Classics of the 80's
	==> Album Name Telecommunications
	   ==> Album Match {'Discogs': 'Telecommunications'}
	==> Album Name Greatest Hits Remixed
	   ==> Album Match {'Discogs': 'Greatest Hits Remixed'}
	==> Album Name I Ran
	==> Album Name Platinum & G

	==> Album Name Dance With Me (Paul Van Dyk remix)
	==> Album Name Elegy
	==> Album Name I Die For You Today
	==> Album Name Song for No One
   ==> Album Type 4
==> Artist Abigor
   ==> Album Type 1
   ==> Album Type 2
	==> Album Name Origo Regium: 1993-1994
	   ==> Album Match {'Discogs': 'Origo Regium 1993-1994'}
	==> Album Name Nachthymnen (From The Twilight Kingdom) / Orkblut - The Retaliation
	   ==> Album Match {'Discogs': 'Nachthymnen (From The Twilight Kingdom) / Orkblut - The Retaliation'}
	==> Album Name Verwüstung / Invoke The Dark Age // Opus IV
	   ==> Album Match {'Discogs': 'Verwüstung / Invoke The Dark Age - Opus IV'}
	==> Album Name Quintessence
	   ==> Album Match {'Discogs': 'Quintessence'}
	==> Album Name Four Keys to a Foul Reich (Songs of Pestilence, Darkness and Death)
	   ==> Album Match {'Discogs': 'Four Keys To A Foul Reich (Songs Of Pestilence, Darkness And Death)'}
   ==> Album Type 3
	==> Album Name Supreme and Immortal Is the Art of the Devil
	   ==> Album

	   ==> Album Match {'AllMusic': 'The Abyss'}
	==> Album Name Life's A Bitch
	   ==> Album Match {'AllMusic': "Life's a Bitch"}
   ==> Album Type 4
==> Artist Ace Of Base
   ==> Album Type 1
   ==> Album Type 2
	==> Album Name Singles of the 90s
	   ==> Album Match {'AllMusic': 'Singles of the 90s'}
	==> Album Name Greatest Hits
	   ==> Album Match {'Discogs': 'Greatest Hits'}
	==> Album Name The Collection
	   ==> Album Match {'Discogs': 'The Collection'}
	==> Album Name Platinum & Gold Collection
	   ==> Album Match {'AllMusic': 'Platinum & Gold Collection'}
	==> Album Name The Ultimate Collection
	   ==> Album Match {'AllMusic': 'The Ultimate Collection'}
	==> Album Name Best of the best music collection - New, best & remixes
	==> Album Name Platinum & Gold
	   ==> Album Match {'Discogs': 'Platinum & Gold'}
	==> Album Name Playlist: The Very Best of Ace of Base
	   ==> Album Match {'AllMusic': 'Playlist: The Very Best of Ace of Base'}
	   ==> Album Match {'AllMusic': 'Playlist: The 

   ==> Album Type 1
   ==> Album Type 2
   ==> Album Type 3
	==> Album Name The Age of Love
	   ==> Album Match {'AllMusic': 'The Age of Love'}
	   ==> Album Match {'AllMusic': 'The Age of Love', 'Discogs': 'The Age Of Love'}
   ==> Album Type 4
==> Artist Agent 99
   ==> Album Type 1
   ==> Album Type 2
	==> Album Name Little Pieces: 1993 - 1995
	   ==> Album Match {'Discogs': 'Little Pieces: 1993-1995'}
   ==> Album Type 3
   ==> Album Type 4
==> Artist Agnostic Front
   ==> Album Type 1
	==> Album Name Live at CBGB
	   ==> Album Match {'Discogs': 'Live At CBGB'}
	==> Album Name Last Warning
	==> Album Name Working Class Heroes
	   ==> Album Match {'AllMusic': 'Working Class Heroes'}
   ==> Album Type 2
	==> Album Name Cause for Alarm / Liberty and Justice For…
	==> Album Name Cause for Alarm / Victim in Pain
	   ==> Album Match {'AllMusic': 'Cause for Alarm/Victim in Pain'}
	   ==> Album Match {'AllMusic': 'Cause for Alarm/Victim in Pain', 'Discogs': 'Cause For Alarm / Victim In Pai

   ==> Album Type 1
	==> Album Name Alannah Myles
	   ==> Album Match {'Discogs': 'Alannah Myles'}
	==> Album Name Rockinghorse
	   ==> Album Match {'Discogs': 'Rockinghorse'}
	==> Album Name Alannah
	==> Album Name Arival
	   ==> Album Match {'Discogs': 'Arival'}
	==> Album Name Black Velvet
	   ==> Album Match {'Discogs': 'Black Velvet'}
   ==> Album Type 2
	==> Album Name The Very Best of Alannah Myles
	   ==> Album Match {'Discogs': 'The Very Best Of Alannah Myles'}
	==> Album Name Myles & More: The Very Best of Alannah Myles
	==> Album Name Alannah/Alannah Myles
	   ==> Album Match {'Discogs': 'Alannah / Alannah Myles'}
   ==> Album Type 3
	==> Album Name Song Instead of a Kiss
	   ==> Album Match {'Discogs': 'Song Instead Of A Kiss'}
	==> Album Name Black Velvet [Single]
	==> Album Name What Are We Waiting For
	   ==> Album Match {'Discogs': 'What Are We Waiting For'}
	==> Album Name Like Flames
	   ==> Album Match {'Discogs': 'Like Flames'}
	==> Album Name Rhino Hi-Five: Alannah

...

   ==> Album Type 4
==> Artist Queen
   ==> Album Type 1
	==> Album Name Live Killers
	   ==> Album Match {'AllMusic': 'Live Killers'}
	==> Album Name Live
	   ==> Album Match {'Discogs': 'Live'}
	==> Album Name Rock in Japan
	==> Album Name Live Magic
	   ==> Album Match {'AllMusic': 'Live Magic'}
	==> Album Name At the Beeb
	   ==> Album Match {'Discogs': 'At The Beeb'}
	==> Album Name Live at Wembley ’86
	==> Album Name Who Wants to Live Forever
	==> Album Name Live at Wembley Stadium
	==> Album Name We Are the Champions: Final Live in Japan
	==> Album Name Queen on Fire: Live at the Bowl
	==> Album Name Rock Montreal
	   ==> Album Match {'Discogs': 'Rock Montreal'}
	==> Album Name Rock You from Rio - Live
	==> Album Name Hungarian Rhapsody: Live in Budapest
	   ==> Album Match {'Discogs': 'Hungarian Rhapsody (Live In Budapest)'}
	==> Album Name Live at the Rainbow ’74
	==> Album Name A Night at the Odeon
	   ==> Album Match {'Discogs': 'A Night At The Odeon'}
   ==> Album Type 2
	=

   ==> Album Type 1
	==> Album Name Good to See You Again, Alice Cooper
	==> Album Name Live From the Astroturf
   ==> Album Type 2
	==> Album Name School Days: The Early Recordings
	==> Album Name Alice Cooper’s Greatest Hits
	   ==> Album Match {'AllMusic': "Alice Cooper's Greatest Hits"}
	==> Album Name The Beast of Alice Cooper
	   ==> Album Match {'AllMusic': 'The Beast of Alice Cooper'}
	   ==> Album Match {'AllMusic': 'The Beast of Alice Cooper', 'Discogs': 'The Beast Of Alice Cooper'}
	==> Album Name The Essentials
	   ==> Album Match {'AllMusic': 'The Essentials'}
	==> Album Name School’s Out and Other Hits
	   ==> Album Match {'AllMusic': "School's Out and Other Hits"}
	==> Album Name Trilogy
	==> Album Name Original Album Series
	   ==> Album Match {'AllMusic': 'Original Album Series'}
	==> Album Name Old School (1964–1974)
	==> Album Name The Triple Album Collection
	   ==> Album Match {'AllMusic': 'Triple Album Collection'}
   ==> Album Type 3
	==> Album Name Eighteen / Bo

	   ==> Album Match {'AllMusic': "Promise Ain't Enough", 'Discogs': "Promises Ain't Enough"}
	==> Album Name Romeo Is Bleeding
	   ==> Album Match {'AllMusic': 'Romeo Is Bleeding'}
   ==> Album Type 4
==> Artist Les Beatniks
==> Artist Meathook Seed
   ==> Album Type 1
   ==> Album Type 2
   ==> Album Type 3
   ==> Album Type 4
==> Artist Starship
   ==> Album Type 1
   ==> Album Type 2
	==> Album Name Greatest Hits: 10 Years and Change
	==> Album Name We Built This City
	   ==> Album Match {'AllMusic': 'We Built This City'}
	==> Album Name Hits
	   ==> Album Match {'Discogs': 'Hits'}
	==> Album Name VH1: Behind the Music Collection
	==> Album Name Platinum and Gold Collection
	   ==> Album Match {'AllMusic': 'Platinum & Gold Collection'}
	==> Album Name Starship: Original Performer Original Songs
	==> Album Name Rock n' Roll Masters: Starship
	==> Album Name Original Album Classics
	   ==> Album Match {'AllMusic': 'Original Album Classics'}
   ==> Album Type 3
	==> Album Name Sara
	  

	   ==> Album Match {'AllMusic': 'Thank You Everyday'}
	==> Album Name Call Me
	   ==> Album Match {'AllMusic': 'Call Me'}
	==> Album Name Picnic in the Summertime
	   ==> Album Match {'AllMusic': 'Picnic in the Summertime'}
	   ==> Album Match {'AllMusic': 'Picnic in the Summertime', 'Discogs': 'Picnic In The Summertime'}
	==> Album Name Rhino Hi-Five: Deee-Lite
	   ==> Album Match {'AllMusic': 'Rhino Hi-Five: Deee-Lite'}
	==> Album Name Groove Is In the Heart EP
   ==> Album Type 4
==> Artist Foals
   ==> Album Type 1
	==> Album Name Live at The Royal Albert Hall
	   ==> Album Match {'Discogs': 'Live At The Royal Albert Hall '}
   ==> Album Type 2
   ==> Album Type 3
	==> Album Name Try This on Your Piano
	   ==> Album Match {'Discogs': 'Try This On Your Piano'}
	==> Album Name Hummer
	   ==> Album Match {'AllMusic': 'Hummer'}
	==> Album Name Mathletics
	   ==> Album Match {'AllMusic': 'Mathletics'}
	==> Album Name Balloons
	   ==> Album Match {'AllMusic': 'Balloons'}
	==> Album Name

	==> Album Name It's Time
	   ==> Album Match {'Discogs': "It's Time"}
	==> Album Name Feels Good
	   ==> Album Match {'Discogs': 'Feels Good'}
	==> Album Name An Idea in Everything
	   ==> Album Match {'Discogs': 'An Idea In Everything'}
	==> Album Name Ready for the Good Times
	==> Album Name A Taste of Wine
   ==> Album Type 2
	==> Album Name The Best of Glenn Jones
	   ==> Album Match {'Discogs': 'The Best Of Glenn Jones'}
	==> Album Name Greatest Hits: Giving Myself to You
	==> Album Name Everybody Loves a Winner/Finesse
	   ==> Album Match {'Discogs': 'Everybody Loves A Winner / Finesse'}
	==> Album Name Forever: Timeless R&B Classics
   ==> Album Type 3
	==> Album Name Can We Try Again
	   ==> Album Match {'Discogs': 'Can We Try Again'}
	==> Album Name Here I Go Again [Single]
	==> Album Name I've Been Searchin'
	==> Album Name Good Thang [Vinyl Single]
	==> Album Name Good Thang [Cassette Single]
	==> Album Name Round & Round
	==> Album Name Let It Rain
	   ==> Album Match {'Di

In [147]:
for artistName, artistData in albumDBMap.items():
    for albumType, albumTypeData in artistData.items():
        for albumName, albumMatches in albumTypeData.items():
            primaryDB = albumMatches["DB"]
            matches   = albumMatches["Match"]
            print("{0: <35}{1: <4}{2: <50}{3: <15}{4}".format(artistName,albumType,albumName,primaryDB, matches))

A Flock Of Seagulls                1   A Flock of Seagulls                               AllMusic       {'Discogs': 'A Flock Of Seagulls'}
A Flock Of Seagulls                1   Listen                                            AllMusic       {'Discogs': 'Listen'}
A Flock Of Seagulls                1   The Story of a Young Heart                        AllMusic       {'Discogs': 'The Story Of A Young Heart'}
A Flock Of Seagulls                1   Dream Come True                                   AllMusic       {'Discogs': 'Dream Come True'}
A Flock Of Seagulls                1   Light at the End of the World                     AllMusic       {}
A Flock Of Seagulls                1   Ascension                                         AllMusic       {'Discogs': 'Ascension'}
A Flock Of Seagulls                2   The Best of A Flock of Seagulls [Jive]            AllMusic       {}
A Flock Of Seagulls                2   Greatest Hits [Jive]                              AllMusic       {}
A Fl

0 MusicBrainz True
1 AllMusic False


In [103]:
num    = 1
cutoff = 0.95


1 6 16
	 A Flock of Seagulls 	 []
	 Listen 	 ['Listen']
	 The Story of a Young Heart 	 []
	 Dream Come True 	 ['Dream Come True']
	 Light at the End of the World 	 []
	 Ascension 	 ['Ascension']
2 21 22
	 The Best of A Flock of Seagulls [Jive] 	 []
	 Greatest Hits [Jive] 	 []
	 Collection 	 []
	 20 Classics of the 80's 	 []
	 Telecommunications 	 ['Telecommunications']
	 Greatest Hits Remixed 	 ['Greatest Hits Remixed']
	 I Ran 	 []
	 Platinum & Gold Collection 	 ['Platinum & Gold Collection']
	 Essential New Wave 	 ['Essential New Wave']
	 I Ran: The Best Of 	 ['I Ran: The Best Of']
	 We Are the '80s 	 []
	 Greatest Hits [Time Music] 	 []
	 Best of A Flock of Seagulls [Direct Source] 	 []
	 Playlist: The Very Best of Flock of Seagulls 	 []
	 Greatest Hits [Legacy] 	 []
	 Space Age Love Songs 	 []
	 Wishing: The Very Best Of 	 []
	 Wishing 	 ['Wishing']
	 Remixes & Rarities 	 ['Remixes & Rarities']
	 Inflight: Extended Essentials 	 []
	 I Ran (So Far Away) 	 []
3 12 31
	 Magic [EP] 	 [

In [97]:
todo

['Discogs']